In [22]:
from keras.datasets import cifar10,mnist
from keras.preprocessing.image import ImageDataGenerator 
from keras.models import Sequential, Model
from keras.layers import Dense, Input, Dropout, Activation, Flatten, LSTM, SimpleRNN, GRU, Embedding
from keras.layers import Convolution2D, MaxPooling2D, normalization
from keras.utils import np_utils
from keras.preprocessing import sequence

import keras.backend as K

In [4]:
from keras.datasets import imdb

(x_train, y_train), (x_test, y_test) = imdb.load_data(path="imdb_full.pkl",
                                                      num_words=None,
                                                      skip_top=0,
                                                      maxlen=None,
                                                      seed=113,
                                                      start_char=1,
                                                      oov_char=2,
                                                      index_from=3)

In [ ]:
from keras.datasets import reuters

(x_train, y_train), (x_test, y_test) = reuters.load_data(path="reuters.pkl",
                                                         num_words=None,
                                                         skip_top=0,
                                                         maxlen=None,
                                                         test_split=0.2,
                                                         seed=113,
                                                         start_char=1,
                                                         oov_char=2,
                                                         index_from=3)

In [23]:
from keras.datasets import boston_housing

(x_train, y_train), (x_test, y_test) = boston_housing.load_data()

In [24]:
top_words = 5000
(X_train, y_train), (X_test, y_test) = imdb.load_data(num_words=top_words)

In [25]:
max_review_length = 500
X_train = sequence.pad_sequences(X_train, maxlen=max_review_length)
X_test = sequence.pad_sequences(X_test, maxlen=max_review_length)

In [26]:
embedding_vector_length = 32
model = Sequential()
model.add(Embedding(top_words, embedding_vector_length, input_length=max_review_length))
#model.add(LSTM(100))
#model.add(Dense(1, activation='sigmoid'))
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
print(model.summary())

TypeError: sigmoid_cross_entropy_with_logits() got an unexpected keyword argument 'labels'

In [13]:
max_features = 20000
maxlen = 80  
batch_size = 32

(x_train, y_train), (x_test, y_test) = imdb.load_data(num_words=max_features)
print(len(x_train), 'train sequences')
print(len(x_test), 'test sequences')

print('Pad sequences (samples x time)')
x_train = sequence.pad_sequences(x_train, maxlen=maxlen)
x_test = sequence.pad_sequences(x_test, maxlen=maxlen)
print('x_train shape:', x_train.shape)
print('x_test shape:', x_test.shape)

Loading data...
(25000, 'train sequences')
(25000, 'test sequences')
Pad sequences (samples x time)
('x_train shape:', (25000, 80))
('x_test shape:', (25000, 80))


In [14]:
x_train

array([[   15,   256,     4, ...,    19,   178,    32],
       [  125,    68,     2, ...,    16,   145,    95],
       [  645,   662,     8, ...,     7,   129,   113],
       ..., 
       [  529,   443, 17793, ...,     4,  3586,     2],
       [  286,  1814,    23, ...,    12,     9,    23],
       [   97,    90,    35, ...,   204,   131,     9]], dtype=int32)

In [18]:
model = Sequential()
model.add(Embedding(max_features, 128))
model.add(LSTM(128))

TypeError: Expected int32, got list containing Tensors of type '_Message' instead.

In [ ]:
model = Sequential()
model.add(Embedding(max_features, 128))
model.add(LSTM(128, dropout=0.2, recurrent_dropout=0.2))

model.add(Dense(1, activation='sigmoid'))

# try using different optimizers and different optimizer configs
model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])

print('Train...')
model.fit(x_train, y_train,
          batch_size=batch_size,
          epochs=15,
          validation_data=(x_test, y_test))
score, acc = model.evaluate(x_test, y_test,
                            batch_size=batch_size)
print('Test score:', score)
print('Test accuracy:', acc)

In [ ]:
# as the first layer in a Sequential model
model = Sequential()
model.add(LSTM(32, input_shape=(10, 64)))
# now model.output_shape == (None, 32)
# note: `None` is the batch dimension.

# for subsequent layers, no need to specify the input size:
model.add(LSTM(16))

# to stack recurrent layers, you must use return_sequences=True
# on any recurrent layer that feeds into another recurrent layer.
# note that you only need to specify the input size on the first layer.
model = Sequential()
model.add(LSTM(64, input_dim=64, input_length=10, return_sequences=True))
model.add(LSTM(32, return_sequences=True))
model.add(LSTM(10))

In [ ]:
model = Sequential()
model.add(Embedding(1000, 64, input_length=10))
# the model will take as input an integer matrix of size (batch, input_length).
# the largest integer (i.e. word index) in the input should be no larger than 999 (vocabulary size).
# now model.output_shape == (None, 10, 64), where None is the batch dimension.

input_array = np.random.randint(1000, size=(32, 10))

model.compile('rmsprop', 'mse')
output_array = model.predict(input_array)
assert output_array.shape == (32, 10, 64)

In [ ]:
if not data_augmentation: 
    print('Not using data augmentation.')    
    model.fit(X_train, Y_train,  batch_size=batch_size, nb_epoch=nb_epoch,
              validation_data=(X_test, Y_test),  shuffle=True)
else:
    print('Using real-time data augmentation.')    
    datagen = ImageDataGenerator( 
        featurewise_center=False,  # set input mean to 0 over the dataset 
        samplewise_center=False,  # set each sample mean to 0 
        featurewise_std_normalization=False,  # divide inputs by std of the dataset 
        samplewise_std_normalization=False,  # divide each input by its std 
        zca_whitening=False,  # apply ZCA whitening        
        rotation_range=0,  # randomly rotate images in the range (0..180 deg)        
        width_shift_range=0.1,  # randomly shift images horizontally (fraction of total width)        
        height_shift_range=0.1,  # randomly shift images vertically (fraction of total height)        
        horizontal_flip=True,  # randomly flip images 
        vertical_flip=False  # randomly flip images    
        )
    datagen.fit(X_train)    # Fit the model on the batches generated by datagen.flow().
    model.fit_generator(datagen.flow(X_train, Y_train, 
                                     batch_size=batch_size), samples_per_epoch=X_train.shape[0],
                                     nb_epoch=nb_epoch, validation_data=(X_test, Y_test))


Not using data augmentation.
Train on 50000 samples, validate on 10000 samples
Epoch 1/10
 1120/50000 [..............................] - ETA: 408s - loss: 2.3128 - acc: 0.0902